### Lab 2 - TSP problem

In [80]:
import pandas as pd
import random as random
from concurrent.futures import ProcessPoolExecutor, as_completed
import multiprocessing
import numpy as np
from tqdm import tqdm

In [2]:
cities = pd.read_csv("cities/italy.csv", header=None, names=["city", "x", "y"])

Greedy approach: for each city in __cities__, compute the following steps:
1) start from that city and save it as __current_city__;
2) for each city that has not been visited yet, compute the euclidean distance between it and the __current_city__;
3) find the __closest_city__ to the current one as the one who has the __min_distance__;
4) update the __totale_distance__ summing up all the minimun distances computed;
5) save in a dictionary an element __city__: (__path__, __total_distance__).

After having compute this for each city, choose the solution that has the minimun __totale_distance__.

In [213]:
def distance(city1, city2):
    return ((city1.x - city2.x)**2 + (city1.y - city2.y)**2)**0.5

def tsp_greedy(cities):
    # for each city, run the greedy algorithm and keep track of the best solution in a dictionary with the city as key,
    # the path of the visited cities and the total distance as value
    dict_city_solution = {}

    for starting_city in cities.itertuples():
        current_city = starting_city

        # define a list of visited cities and add the starting city
        path = [starting_city.city]

        # define a list of cities to visit and remove the starting city
        cities_to_visit = cities[cities.city != starting_city.city]

        # initialize the total distance
        total_distance = 0

        # for each city to visit, find the closest city and add it to the path, 
        # then move to that city and remove it from the cities to visit
        while not cities_to_visit.empty:
            cities_to_visit = cities_to_visit[cities_to_visit.city != current_city.city]

            # find the closest city
            closest_city = None
            min_distance = float('inf')

            for city in cities_to_visit.itertuples():
                dist = distance(current_city, city)
                if dist < min_distance:
                    closest_city = city
                    min_distance = dist

            # check if a closest city was found
            if closest_city is not None:
                total_distance += min_distance
                current_city = closest_city
                path.append(current_city.city)

        # add the distance from the last city to the starting one
        total_distance += distance(current_city, starting_city)

        # save the city and the solution in the dictionary
        dict_city_solution[starting_city.city] = (path, total_distance)

    # find the best solution
    best_solution = None
    best_distance = float('inf')

    # for each city, check if the total distance is better than the best distance
    for city, (path, total_distance) in dict_city_solution.items():
        if total_distance < best_distance:
            best_distance = total_distance
            best_solution = path

    # return just the paths ranked by descending distance (used later for the genetic algorithm)
    path_distance = list(dict_city_solution.values())
    path_distance.sort(key=lambda x: x[1], reverse=False)
    sorted_path_greedy = [x[0] for x in path_distance]

    return best_solution, best_distance, sorted_path_greedy
    
best_solution_greedy, best_distance_greedy, sorted_path_greedy = tsp_greedy(cities)
print("Best solution: ", best_solution_greedy)
print(f"Best distance: {best_distance_greedy*100:.2f}")
print("Sorted paths: ", sorted_path_greedy)

Best solution:  ['Trieste', 'Venice', 'Padua', 'Vicenza', 'Verona', 'Trento', 'Bolzano', 'Brescia', 'Bergamo', 'Monza', 'Milan', 'Novara', 'Turin', 'Genoa', 'Piacenza', 'Parma', "Reggio nell'Emilia", 'Modena', 'Bologna', 'Ferrara', 'Ravenna', 'Forlì', 'Rimini', 'Perugia', 'Terni', 'Rome', 'Latina', 'Giugliano in Campania', 'Naples', 'Salerno', 'Foggia', 'Andria', 'Bari', 'Taranto', 'Messina', 'Reggio di Calabria', 'Catania', 'Syracuse', 'Palermo', 'Cagliari', 'Sassari', 'Leghorn', 'Prato', 'Florence', 'Ancona', 'Pescara']
Best distance: 4607.54
Sorted paths:  [['Trieste', 'Venice', 'Padua', 'Vicenza', 'Verona', 'Trento', 'Bolzano', 'Brescia', 'Bergamo', 'Monza', 'Milan', 'Novara', 'Turin', 'Genoa', 'Piacenza', 'Parma', "Reggio nell'Emilia", 'Modena', 'Bologna', 'Ferrara', 'Ravenna', 'Forlì', 'Rimini', 'Perugia', 'Terni', 'Rome', 'Latina', 'Giugliano in Campania', 'Naples', 'Salerno', 'Foggia', 'Andria', 'Bari', 'Taranto', 'Messina', 'Reggio di Calabria', 'Catania', 'Syracuse', 'Palermo

Genetic algorithm approach: to find the shortest path among cities in `cities`, perform the following steps:

1) generate a random population of paths, each representing a unique order (permutation) of cities;

2) for each path, compute the __total_distance__ as the sum of Euclidean distances between consecutive cities, including the return to the starting city. Calculate __fitness__ as the inverse of __total_distance__;

3) perform __tournament selection__ to choose two parent paths based on highest fitness (shortest distance);

4) for each pair of parents, use __order crossover__ to create two children;

5) apply __swap mutation__ on each child with a small probability, swapping two cities in the path to introduce diversity;

6) keep elite individuals (paths with the shortest distances) from the previous generation, then fill the rest of the population with newly generated children.

After completing all generations, find and return the path with the __min_total_distance__ across all individuals in the final population.


In [ ]:
BEST_SOLUTION_GREEDY = sorted_path_greedy
LIST_CITY = cities['city'].tolist()
LIST_CITY_SIZE = len(LIST_CITY)
POPULATION_SIZE = 100
ELITE_NUMBER = 10
MUTATION_RATE = 0.05
NUM_GENERATIONS = 200

def distance(city1, city2):
    distance = ((city1[0] - city2[0])**2 + (city1[1] - city2[1])**2)**0.5
    return distance

def compute_distance_from_fintness(fitness_values):
    return [1/fitness for fitness in fitness_values]

# compute fitness of an individual
def fitness(individual):
    total_distance = 0
    for i in range(len(individual)):
        city1 = cities[cities['city'] == individual[i]]
        city2 = cities[cities['city'] == individual[(i+1) % len(individual)]]
        
        city1_x, city1_y = float(city1.iloc[0]['x']), float(city1.iloc[0]['y'])
        city2_x, city2_y = float(city2.iloc[0]['x']), float(city2.iloc[0]['y'])

        total_distance += distance((city1_x, city1_y), (city2_x, city2_y))

    return float(1 / total_distance)


# compute fitness of the population
def compute_fitness(population):
    fitness_values = []
    for individual in population:
        fitness_values.append(fitness(individual))
    return fitness_values

def valid_solution(individual):
    # check if all cities are explored and there are no duplicates
    if len(set(individual)) != len(individual):
        return False
    return True

def mutation(individual):
    r = random.random()
    if r < MUTATION_RATE:
        pos1, pos2 = random.sample(range(1, len(individual) - 1), 2)
        individual[pos1], individual[pos2] = individual[pos2], individual[pos1]
        if len(set(individual)) != len(individual):
            return individual
    return individual


def generate_population():
    # initialize the population with the individual obtained with the greedy algorithm applying a mutation,
    # then generate the remaining individuals randomly
    population = []
    for i in range(POPULATION_SIZE):
        if i < ELITE_NUMBER:
            individual = BEST_SOLUTION_GREEDY[i]
            population.append(individual)
        else:
            individual = random.sample(LIST_CITY, LIST_CITY_SIZE)
            while not valid_solution(individual):
                individual = random.sample(LIST_CITY, LIST_CITY_SIZE)
            population.append(individual)

    return population

def crossover(parent1, parent2):
    size = len(parent1)
    start, end = sorted(random.sample(range(size), 2))
    child = [None] * size

    child[start:end + 1] = parent1[start:end + 1]

    index = (end + 1) % size
    for gene in parent2:
        if gene not in child and child[index] is None:
            child[index] = gene
            index = (index + 1) % size

    return child

def parent_selection(population, fitness_scores):
    selected = random.choices(population, weights=fitness_scores, k=POPULATION_SIZE)
    return selected

def evolve_population(population):
    # order the population by fitness
    population.sort(key=lambda individual: fitness(individual), reverse=True)

    # keep the elite individuals
    elite = population[:ELITE_NUMBER]

    # parent selection
    parents_list = parent_selection(population, compute_fitness(population))

    new_population = []

    # apply crossover
    for i in range(POPULATION_SIZE):
        new_population.append(mutation(crossover(parents_list[i], parents_list[(i+1) % POPULATION_SIZE])))



    return new_population

def genetic_algorithm():
    population = generate_population()
    best_solution = None
    best_distance = float('inf')

    for generation in range(NUM_GENERATIONS):
        print(f"Generation {generation + 1}/{NUM_GENERATIONS}...")

        new_population = evolve_population(population)

        # order the population by fitness
        population.sort(key=lambda individual: fitness(individual), reverse=True)

        # keep the elite individuals
        elite = population[:ELITE_NUMBER]

        # combine the elite individuals with the new population
        population = elite + new_population
        population = population[:POPULATION_SIZE]
        fitness_values = compute_fitness(population)

        print(f"Population: {population}")

        print()

    best_solution_index = fitness_values.index(max(fitness_values))
    best_distance = 1 / fitness_values[best_solution_index]
    best_solution = population[best_solution_index]
    
    return best_solution, best_distance

if __name__ == "__main__":
    best_solution, best_distance = genetic_algorithm()
    print("Best solution: ", best_solution)
    print(f"Best distance: {best_distance*100:.2f}")


Generation 1/100
population:  [['Trieste', 'Venice', 'Padua', 'Vicenza', 'Verona', 'Trento', 'Bolzano', 'Brescia', 'Bergamo', 'Monza', 'Milan', 'Novara', 'Turin', 'Genoa', 'Piacenza', 'Parma', "Reggio nell'Emilia", 'Modena', 'Bologna', 'Ferrara', 'Ravenna', 'Forlì', 'Rimini', 'Perugia', 'Terni', 'Rome', 'Latina', 'Giugliano in Campania', 'Naples', 'Salerno', 'Foggia', 'Andria', 'Bari', 'Taranto', 'Messina', 'Reggio di Calabria', 'Catania', 'Syracuse', 'Palermo', 'Cagliari', 'Sassari', 'Leghorn', 'Prato', 'Florence', 'Ancona', 'Pescara'], ['Venice', 'Padua', 'Vicenza', 'Verona', 'Trento', 'Bolzano', 'Brescia', 'Bergamo', 'Monza', 'Milan', 'Novara', 'Turin', 'Genoa', 'Piacenza', 'Parma', "Reggio nell'Emilia", 'Modena', 'Bologna', 'Ferrara', 'Ravenna', 'Forlì', 'Rimini', 'Perugia', 'Terni', 'Rome', 'Latina', 'Giugliano in Campania', 'Naples', 'Salerno', 'Foggia', 'Andria', 'Bari', 'Taranto', 'Messina', 'Reggio di Calabria', 'Catania', 'Syracuse', 'Palermo', 'Cagliari', 'Sassari', 'Leghorn